# Test CRAWDAD User

TJ Kim

Date: 4/20/21

#### Summary:
Import and run Crawdad users.

In [1]:
# Import Generic Classes
import numpy as np
import copy
import random

# Import All Custom Classes
import os, sys
sys.path.append(os.path.pardir+"/solvers")
sys.path.append(os.path.pardir+"/one_mobility")
sys.path.append(os.path.pardir+"/crawdad_mobility")


from Server import *
from User import *
from Link import *
from Job import *
from get_one_sim_usr import *
from load_crawdad_usr import *

# Import Solver Classes
from Optim_PlanGenerator import *
from SeqGreedy_PlanGenerator import*
from Migration_Plans import *

In [2]:
# Load All 12 users and trim their info
db_names = []
for i in range(1,13):
    db_names += ['LifeMap_GS'+str(i)+'.db']
    
db = []
for name in db_names:
    name = '/home/tkim/CMU/MEC_research/crawdad_mobility/' + name
    df,trace = load_usr(name)
    db += [trace]

In [3]:
"""
Make Simulation Parameters
"""
sim_param = Sim_Params(time_steps=15, x_length = 7, y_length = 11, max_edge_length=3,num_path_limit=10)
boundaries = np.array([[-sim_param.x_length,sim_param.x_length],[sim_param.y_length,sim_param.y_length]])

"""
Make Servers
"""

# Server Settings
num_server_l1 = 2
num_server_l2 = 6
num_server_l3 = 1

num_resource = 3
weak_range = np.array([[4,8],[1000,1500],[4,16]])
strong_range = np.array([[50,100],[100000,150000],[300,600]])

rsrc_cost = np.array([0.03, 0.01, 0.05])

rsrc_cost_scale_lv1 = 2
rsrc_cost_scale_lv2 = 1
rsrc_cost_scale_lv3 = 0.7

# Generate Server
servers_l1 = []
servers_l2 = []
servers_l3 = []
idx_counter = 0

for i in range(num_server_l1):
    servers_l1.append(Server(boundaries,level=1,rand_locs=True,locs=None))
    servers_l1[-1].server_resources(num_resource, weak_range, strong_range)
    servers_l1[-1].assign_id(idx_counter)
    servers_l1[-1].server_resources_cost(num_resource,rsrc_cost*rsrc_cost_scale_lv1)
    idx_counter += 1

for i in range(num_server_l2):
    servers_l2.append(Server(boundaries,level=2,rand_locs=True,locs=None))
    servers_l2[-1].server_resources(num_resource, weak_range, strong_range)
    servers_l2[-1].assign_id(idx_counter)
    servers_l2[-1].server_resources_cost(num_resource,rsrc_cost*rsrc_cost_scale_lv2)
    idx_counter += 1

for i in range(num_server_l3):
    servers_l3.append(Server(boundaries,level=3,rand_locs=False,locs=np.array([200,200])))
    servers_l3[-1].server_resources(num_resource, weak_range, strong_range)
    servers_l3[-1].assign_id(idx_counter)
    servers_l3[-1].server_resources_cost(num_resource,rsrc_cost*rsrc_cost_scale_lv3)
    idx_counter += 1

servers = servers_l1 + servers_l2 + servers_l3


"""
Make Links
"""

# Link Settings
num_link = [0,1,2,3]
prob_link = [0.5,0.2,0.2,0.1]
lv_minmax = np.array(([[500,1000],[10000,20000],[30000,50000]]))
lv1_transmission = 1
link_costs = np.array([0.05, 0.02, 0.01])
latency_settings = [10, 1] #[ms per switch, ms per mile]

links = Link(servers, num_link, prob_link, lv_minmax, link_costs, latency_settings,lv1_transmission)


In [6]:
"""
Make Users 
- First draw samples from dataste - 
"""

# User Settings
num_user = 1

max_speed = 80
num_path = 5
num_path_orig = 1

# Generate Server
users = []
idx_counter = 0

for i in range(num_user):
    
    comfirmed = False
    
    while (not comfirmed):
        db_idx = np.random.randint(len(db))
        mvmt_array = random.choice(list(db[db_idx].values()))
        print(mvmt_array.shape[0])
        if mvmt_array.shape[0] > sim_param.time_steps:
            comfirmed = True
        
    users += [Crawdad_User(boundaries, sim_param.time_steps, max_speed, num_path, num_path_orig, mvmt_array)]
    users[-1].generate_MC(servers)
    users[-1].assign_id(idx_counter)
    idx_counter += 1
    
    



139
215
175
191
111
230
175
69
250
148
29
244
160
287
211
289
260
5
284
155
114
123
160
119
187
149
122
259
36
150
142
141
148
94
131
184
156
211
172
1
122
4
249
215
250
246
165
138
208
277
173
238
148
222
193
206
157
192
238
244
1
196
154
151
155
128
12
277
142
152
264
42
148
286
224
183
63
87
249
158
193
150
165
287
39
15
152
47
264
71
214
130
244
196
136
201
254
37
149
16
144
158
144
105
288
5
145
154
244
173
245
168
196
135
240
251
243
27
281
43
154
217
161
249
90
135
90
244
180
148
236
142
288
270
150
1
187
245
4
107
174
268
287
10
181
259
123
206
124
219
265
47
183
160
112
249
149
260
106
260
1
40
137
62
285
288
154
137
176
94
144
163
268
12
55
103
129
287
129
242
186
113
178
125
251
55
268
251
185
238
263
159
270
190
12
89
165
250
141
139
175
156
285
146
245
256
284
143
148
122
140
126
12
137
144
6
270
6
205
118
4
145
284
12
1
88
142
207
143
25
201
81
200
281
170
260
287
184
288
111
80
287
235
222
192
116
152
83
110
70
122
27
141
158
178
272
176
138
244
156
196
239
3
211
127
150

107
118
170
180
111
147
180
65
16
202
179
177
2
106
156
30
139
141
165
152
156
118
90
177
4
274
280
167
127
179
154
158
118
205
183
128
260
142
238
246
165
91
188
213
277
240
173
124
214
168
285
200
265
243
245
154
121
268
132
151
146
191
127
156
3
114
269
258
81
124
165
275
169
202
173
124
191
178
153
109
163
156
275
104
232
55
158
245
151
95
281
226
248
182
210
152
260
189
58
189
179
157
127
152
119
189
229
288
192
200
149
137
217
98
289
266
258
88
158
43
27
187
133
144
159
159
288
21
148
44
118
157
231
155
55
116
203
270
55
145
154
264
94
141
165
94
12
123
83
99
246
137
13
280
9
288
287
1
79
153
63
37
165
244
249
7
144
166
168
15
125
145
176
287
157
211
1
119
97
40
47
15
157
87
252
269
164
138
183
243
113
236
55
137
31
124
281
90
119
253
96
262
284
47
4
132
185
244
1
269
1
213
146
281
249
147
252
222
114
153
55
211
155
260
47
238
193
236
27
246
129
60
172
7
183
283
165
284
113
201
1
268
183
120
112
22
1
142
157
260
170
146
282
183
178
191
222
178
238
94
65
272
150
140
263
159
254
12

197
286
289
114
223
146
7
267
277
142
138
258
170
4
36
264
224
270
193
268
215
15
287
180
182
206
278
65
193
8
245
55
260
243
260
118
156
195
74
168
96
244
112
255
231
178
149
180
180
55
286
268
148
287
147
196
157
144
183
31
75
148
122
6
127
16
22
94
243
281
55
80
166
182
94
154
136
129
226
140
88
1
120
127
10
81
32
236
185
277
289
114
284
220
138
183
127
173
172
162
163
270
52
200
165
270
146
1
252
129
265
1
178
127
117
177
55
151
163
170
173
105
151
273
4
287
256
209
165
132
129
151
80
181
37
93
1
55
100
28
265
155
246
142
231
214
142
114
39
135
148
176
147
157
32
177
223
104
260
289
148
196
216
271
149
103
269
12
282
138
149
175
245
51
22
21
176
2
145
177
181
185
12
216
6
22
99
172
87
94
1
263
171
55
192
244
236
122
156
128
207
182
155
123
144
260
151
42
43
285
263
257
168
236
116
154
244
149
273
54
50
179
287
23
12
1
36
144
1
136
138
163
260
128
34
173
246
244
113
223
213
5
267
206
4
117
217
285
94
112
111
113
288
12
238
55
99
56
164
284
149
12
4
178
259
288
25
142
103
36
169
45
2

140
171
155
213
264
158
118
1
12
284
209
177
143
236
3
129
261
274
79
155
185
147
122
124
15
287
277
168
239
142
189
3
116
269
250
45
113
99
273
161
248
149
123
177
163
92
94
112
288
144
269
275
265
283
1
4
44
132
161
149
133
149
4
145
137
238
284
192
5
119
165
154
6
236
206
281
5
180
124
15
215
287
114
12
157
115
175
57
258
166
129
7
28
154
168
147
270
166
147
114
79
164
289
196
165
122
288
19
156
283
139
173
170
142
245
265
183
150
138
147
139
179
281
12
286
150
113
78
140
161
116
122
244
54
266
174
144
27
134
177
230
3
238
135
38
137
153
273
167
241
285
219
151
22
192
162
263
198
123
83
244
263
287
105
235
107
157
253
284
261
129
287
152
176
24
115
90
263
146
168
140
275
206
227
4
183
165
238
254
172
175
6
217
139
269
184
156
142
163
158
135
288
287
181
246
180
64
154
268
165
287
245
55
277
150
179
157
143
149
200
236
168
241
96
153
210
148
287
91
42
197
92
180
154
284
111
284
153
241
238
126
95
182
13
134
39
203
9
161
284
185
99
260
79
128
288
116
154
94
145
252
105
158
36
192
142


177
137
158
145
162
221
249
190
185
152
168
270
13
165
178
225
165
136
211
275
205
113
274
107
236
235
289
269
81
144
27
210
118
192
288
207
287
183
285
288
17
281
55
107
114
36
156
193
83
1
22
123
244
261
1
27
139
133
265
273
145
113
16
122
140
116
113
241
84
264
1
94
264
56
102
26
260
283
88
261
1
24
261
160
172
115
13
215
135
119
288
107
112
36
249
1
240
170
25
219
154
179
118
192
201
224
7
245
135
27
146
124
188
279
206
289
3
149
181
151
155
159
275
5
1
289
215
137
155
133
12
164
158
168
270
22
175
284
267
191
153
288
287
167
283
269
151
275
265
124
13
30
247
100
94
138
169
157
155
1
122
154
116
32
104
87
144
288
57
259
284
144
99
90
17
149
114
57
105
147
55
263
12
154
98
242
195
159
7
1
60
1
213
151
1
133
104
263
27
98
135
114
285
159
215
196
137
38
177
108
188
1
27
173
163
202
147
120
12
133
241
277
113
158
148
98
38
157
266
125
254
146
214
265
142
1
80
287
4
124
286
223
198
171
238
248
129
96
202
39
215
100
187
205
151
288
120
156
7
99
38
167
113
21
153
131
53
116
19
124
206
230

...

180
1
139
181
69
239
92
152
121
157
3
168
105
127
223
210
248
156
35
269
132
270
180
156
113
165
99
140
241
193
231
288
4
62
149
24
270
39
146
273
263
190
104
261
249
178
188
105
42
19
217
91
154
263
287
121
91
142
259
153
1
124
117
178
135
180
96
160
289
258
94
258
177
120
187
263
93
68
236
211
205
153
111
248
129
147
136
39
17
191
160
28
98
283
270
134
261
223
254
148
205
232
164
34
109
159
260
122
144
214
154
231
121
207
107
114
267
148
151
149
29
201
287
203
164
272
287
22
121
117
202
67
203
164
238
160
273
162
154
165
36
130
284
285
141
171
85
28
55
168
42
15
55
156
139
133
43
140
82
54
142
116
126
210
139
125
160
207
124
195
4
252
284
69
287
259
99
4
75
273
1
151
288
150
43
149
63
155
9
171
184
1
149
248
172
48
120
178
287
283
166
166
27
120
187
193
236
1
135
205
289
278
149
255
149
201
1
257
165
94
151
287
252
110
226
83
164
152
128
245
17
42
288
275
145
100
150
163
89
39
130
201
43
79
238
287
241
145
137
100
235
128
74
36
169
68
168
168
273
216
284
249
244
289
271
281
280
145
1

64
91
43
97
156
153
21
113
139
172
1
134
1
287
42
180
156
289
176
251
148
147
207
281
277
36
168
154
288
179
132
142
194
142
69
71
36
289
193
269
93
126
152
13
265
274
147
157
288
197
270
107
126
175
160
1
274
7
203
245
194
142
142
1
164
189
226
79
68
1
250
178
168
102
20
266
128
131
288
255
137
4
154
6
126
1
121
126
279
4
112
165
158
238
240
98
288
283
135
261
124
134
125
190
272
27
39
155
103
168
133
95
162
135
188
184
177
65
153
232
172
8
166
78
134
270
140
148
1
152
154
27
154
128
30
88
161
154
102
214
253
31
151
112
1
238
155
287
169
175
285
287
159
285
80
148
171
5
133
154
25
284
10
15
7
217
194
107
238
1
277
125
181
114
144
170
123
166
231
151
249
275
1
230
190
219
118
94
165
185
149
271
140
135
154
152
266
128
94
266
194
217
133
260
286
158
124
236
130
152
115
244
104
169
155
288
265
170
203
245
116
211
143
230
181
113
189
246
137
147
257
224
135
84
238
158
144
281
88
202
277
112
231
13
5
94
38
142
112
264
34
47
173
285
284
245
175
1
258
189
273
189
144
220
126
173
181
55
107
6

202
269
79
62
43
107
124
179
245
249
284
152
150
193
219
1
269
288
147
185
146
217
168
112
151
284
150
279
13
142
5
168
183
124
135
158
173
287
189
201
111
178
183
288
282
287
137
265
174
145
127
175
287
154
194
245
144
148
171
202
265
164
287
217
155
216
244
258
83
185
253
190
148
251
15
287
144
178
217
5
36
145
80
196
98
65
19
142
140
264
36
157
200
189
289
261
173
285
100
156
144
136
98
89
285
244
216
272
140
238
246
113
5
153
281
247
156
251
140
15
225
249
3
68
231
147
237
274
288
284
12
144
265
60
12
148
157
120
133
139
178
124
146
10
179
265
185
276
128
181
287
114
94
283
231
181
200
130
168
165
15
155
54
135
246
149
141
182
284
137
183
150
277
244
269
47
139
206
210
94
116
135
186
269
235
6
260
178
55
288
168
288
130
93
149
147
243
146
151
289
151
289
3
148
267
172
277
135
1
259
198
247
172
117
239
4
105
139
1
25
192
123
94
278
38
129
249
258
7
263
232
185
150
139
288
254
216
151
103
43
190
81
275
288
130
165
239
217
129
10
160
105
177
147
282
129
39
1
47
114
203
132
245
158
60


152
145
92
128
287
284
87
130
284
88
99
185
160
156
164
258
253
287
271
220
147
269
156
135
25
126
153
179
287
288
84
165
152
288
1
40
36
105
211
108
165
165
4
12
239
260
284
188
221
127
219
110
259
124
288
173
157
288
142
149
245
172
235
133
112
172
107
160
148
165
149
265
284
169
151
288
147
149
155
239
152
195
212
165
284
275
244
278
165
126
190
176
254
113
206
245
151
280
179
267
287
200
192
121
174
235
3
172
226
275
142
141
176
235
139
176
164
287
203
288
118
241
258
125
12
138
288
12
284
155
238
249
288
132
244
4
216
4
217
38
98
130
148
288
128
154
243
142
31
181
279
10
277
179
205
117
236
169
132
239
177
288
139
141
66
255
170
145
223
23
99
27
271
197
266
151
114
131
133
238
236
266
235
195
152
280
176
279
215
47
275
271
165
165
94
284
154
53
205
145
238
288
148
116
167
50
31
7
211
1
279
137
160
124
249
215
165
223
55
136
39
277
203
32
10
263
126
147
283
163
114
149
147
149
272
154
252
154
157
189
141
260
159
172
130
138
12
278
223
47
154
99
155
152
121
13
134
112
113
270
287
17

KeyboardInterrupt: 

In [7]:
confirmed

True

In [8]:
mvmt_array.shape[0] > sim_param.time_steps

True